In [ ]:
%matplotlib inline
import sys
import os
import torch
import torch.nn as nn
import matplotlib.pyplot as plt

rootdir = os.path.abspath(sys.path[0] + '/../')
sys.path.append(rootdir)

torch.cuda.set_device(3)
print("Set CUDA:%d as current device." % torch.cuda.current_device())
torch.autograd.set_grad_enabled(False)

import model
from data import Dataset
from utils import netio, img, device
from utils.view import *
from utils.type import PathLike
from components.fnr import FoveatedNeuralRenderer
from components.render import render


def load_model(model_path: PathLike):
    return model.deserialize(netio.load_checkpoint(model_path)[0],
                             raymarching_early_stop_tolerance=0.01,
                             raymarching_chunk_size_or_sections=None,
                             perturb_sample=False).eval().to(device.default())


def find_file(prefix):
    for path in os.listdir():
        if path.startswith(prefix):
            return path
    return None


def create_renderer(*nets, fov_scale=1.):
    fov_list = [20, 45, 110]
    for i in range(len(fov_list)):
        fov_list[i] = length2fov(fov2length(fov_list[i]) * fov_scale)
    res_list = [(256, 256), (256, 256), (256, 230)]
    res_full = (1600, 1440)
    return FoveatedNeuralRenderer(fov_list, res_list, nn.ModuleList(nets), res_full,
                                  device=device.default())


def plot_images(images):
    plt.figure(figsize=(12, 4))
    plt.subplot(131)
    img.plot(images['layers_img'][0])
    plt.subplot(132)
    img.plot(images['layers_img'][1])
    plt.subplot(133)
    img.plot(images['layers_img'][2])
    #plt.figure(figsize=(12, 12))
    # img.plot(images['overlaid'])
    #plt.figure(figsize=(12, 12))
    # img.plot(images['blended_raw'])
    plt.figure(figsize=(12, 12))
    img.plot(images['blended'])


def save_images(images, scene, i):
    outputdir = '../__demo/mono/'
    os.makedirs(outputdir, exist_ok=True)
    for layer in range(len(images["layers_img"])):
        img.save(images['layers_img'][layer], f'{outputdir}{scene}_{i:04d}({layer}).png')
    img.save(images['blended'], f'{outputdir}{scene}_{i:04d}.png')
    if "overlaid" in images:
        img.save(images['overlaid'], f'{outputdir}{scene}_{i:04d}_overlaid.png')
    if "blended_raw" in images:
        img.save(images['blended_raw'], f'{outputdir}{scene}_{i:04d}_noCE.png')
    if "nerf" in images:
        img.save(images['nerf'], f'{outputdir}{scene}_{i:04d}_nerf.png')


scenes = {
    'classroom': '__new/classroom_all',
    'stones': '__new/stones_all',
    'barbershop': '__new/barbershop_all',
    'lobby': '__new/lobby_all',
    "bedroom2": "__captured/bedroom2"
}


scene = "bedroom2"
os.chdir(f'{rootdir}/data/{scenes[scene]}')
print('Change working directory to ', os.getcwd())

fovea_net = load_model(find_file('fovea'))
periph_net = load_model(find_file('periph'))
nerf_net = load_model(find_file("nerf"))

In [ ]:
params = {
    'classroom': [
        #[0, 0, 0,   -53, 0,   0, 0],
        
        #For Eval
        [0, 0, 0,   0, 0,   0, 0],
        [0, 0, 0,   20, -20,   0, 0],
        [-0.03, 0, 0, 0, 0, 0, -83],
        [0.03, 0, 0, 0, 0, 0, -83],
        [0.3, 0, 0.3, 0, 0], # For panorama (Trans)
        [-0.3, -0.3, -0.3, 0, 0], # For panorama (Trans)
        [0, -0.3, 0.3, 0, 10, 0, 0], # For panorama (V-D)
        [0, 0.3, 0.3, 0, 10, 0, 0], # For panorama (V-D)
        [0, 0.3, 0.3, 0, 10, 160, 350], # For panorama (New)
        
        # For fig latency-quality
        #[0, 0, 0,   10, -13,   0, 0], 
    ],
    'stones': [
        #[0, 0, 0, 0, 10, -300, -50],
        #[0, 0, 0, 0, 10, 200, -50],
        #For Eval
        [-0.5, -0.5, -0.5, -25, 0, 50, -230],
        [-0.5, -0.5, -0.5, 0, 0, 280, -220],
        [-0.5, 0, 0.0, -30, 5, 0, 0],
    ],
    'barbershop': [
        #[0, 0, 0,   0, 0,   0, 0],
        #[0, 0, 0, 20, 0, -300, 50], #For fig rendering-system
        #[0, 0, 0, -140, -30, 150, -250],
        #[0, 0, 0, -60, -30, 75, -125],
        #For Teaser & Eval
        [0, 0, 0,   20, 10,   0, 0],
        [0, 0, 0,   -20, -10,   0, 0],
        [0.15, 0, 0.15,   -13, -5,   0, 0],
        [-0.15, -0.15, 0, 12, 12, 0, 0],
        [-0.15, 0, 0.15, -35, 2, 0, 0],
        [0, 0.15, 0.15, -13, 10, 0, 0],
        [0.15, 0.15, 0, 43, 2, 0, 0],
        [-0.15, 0.15, 0.15, -53, -21, 0, 0],
        [-0.15, 0.15, 0.15, -53, -21, 200, -200]
    ],
    'lobby': [
        #[0, 0, 0, 0, 0, 75, 0],
        #[0, 0, 0, 0, 0, 5, 150],
        #[0.5, 0, 0.5, 29, -12, 0, 0],
        #For Eval
        [-0.5, -0.5, -0.5, -25, 0, -150, 0],
        [-0.5, -0.5, -0.5, 25, 25, -150, 200],
        [-0.03, 0, 0, 0, 0, 75, -20],
        [0.03, 0, 0, 0, 0, 71, -20]
        #[0, 0, 0, -120, 0, 75, 50],
    ]
}

for i, param in enumerate(params[scene]):
    view = Trans(torch.tensor(param[:3], device=device.default()),
                 torch.tensor(euler_to_matrix(-param[4], param[3], 0), device=device.default()).view(3, 3))
    images = renderer(view, param[-2:], using_mask=False, ret_raw=True)
    images['overlaid'] = renderer.foveation.synthesis(images['layers_raw'], param[-2:], do_blend=False)
    if True:
        outputdir = '../__demo/mono/'
        os.makedirs(outputdir, exist_ok=True)
        img.save(images['layers_img'][0], f'{outputdir}{scene}_{i}_fovea.png')
        img.save(images['layers_img'][1], f'{outputdir}{scene}_{i}_mid.png')
        img.save(images['layers_img'][2], f'{outputdir}{scene}_{i}_periph.png')
        img.save(images['blended'], f'{outputdir}{scene}_{i}_blended.png')
        #img.save(images['overlaid'], f'{outputdir}{scene}_{i}_overlaid.png')
        #img.save(images['blended_raw'], f'{outputdir}{scene}_{i}.png')
    else:
        images = plot_images(images)


In [ ]:
def load_views(data_desc_file) -> tuple[list[int], Trans]:
    dataset = Dataset(data_desc_file)
    return dataset.indices.tolist(),\
        Trans(dataset.centers, dataset.rots).to(device.default())


demos = [ # view_idx, center_x, center_y, fov_scale
    [220, 30, 25, 0.7],
    [235, 0, 130, 0.7],
    [239, 70, 140, 0.7],
    [841, -100, 160, 0.7]
]
indices, views = load_views('images.json')
for demo_idx in [0]:
    view_idx = demos[demo_idx][0]
    i = indices.index(view_idx)
    center = tuple(demos[demo_idx][1:3])
    renderer = create_renderer(fovea_net, periph_net, periph_net, fov_scale=demos[demo_idx][3])
    images = renderer(views.get(i), center, using_mask=False)
    #nerf_fovea = render(nerf_net, renderer.cam, views.get(i), None, batch_size=16384)["color"]
    #images["nerf"] = nerf_fovea
    plot_images(images)
    #save_images(images, scene, view_idx)
